# For the Toronto neighborhood data, a Wikipedia page (https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M) exists that has all the information we need to explore and cluster the neighborhoods in Toronto. The Wikipedia page was scrapped and the data wrangled, cleaned, and then read  into a pandas dataframe.

# first part: dataframe will consist of three columns: PostalCode, Borough, and Neighborhood

In [1]:
!pip install geopy
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

!pip install bs4
from bs4 import BeautifulSoup

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.9.2
  latest version: 4.10.1

Please update conda by running

    $ conda update -n base conda



# All requested packages already installed.

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.9.2
  latest version: 4.10.1

Please update conda by running

    $ conda update -n base conda



# All requested packages already installed.

Libraries imported.


In [2]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
html_data = requests.get(url).text

In [3]:
!pip install html5lib
data = BeautifulSoup(html_data,'html.parser')
print(data.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: M - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"91139ba6-ee25-4583-bc18-353f269e219e","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":1019189119,"wgRevisionId":1019189119,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles with short description","Short description is different from Wikidata","Wikipedia

In [4]:
tables = data.find_all('table') 
len(tables)

3

In [5]:
for index,table in enumerate(tables):
    if ("Toronto" in str(table)):
        table_index = index
print(tables[table_index].prettify())

<table cellpadding="2" cellspacing="0" rules="all" style="width:100%; border-collapse:collapse; border:1px solid #ccc;">
 <tbody>
  <tr>
   <td style="width:11%; vertical-align:top; color:#ccc;">
    <p>
     <b>
      M1A
     </b>
     <br/>
     <span style="font-size:85%;">
      <i>
       Not assigned
      </i>
     </span>
    </p>
   </td>
   <td style="width:11%; vertical-align:top; color:#ccc;">
    <p>
     <b>
      M2A
     </b>
     <br/>
     <span style="font-size:85%;">
      <i>
       Not assigned
      </i>
     </span>
    </p>
   </td>
   <td style="width:11%; vertical-align:top;">
    <p>
     <b>
      M3A
     </b>
     <br/>
     <span style="font-size:85%;">
      <a href="/wiki/North_York" title="North York">
       North York
      </a>
      <br/>
      (
      <a href="/wiki/Parkwoods" title="Parkwoods">
       Parkwoods
      </a>
      )
     </span>
    </p>
   </td>
   <td style="width:11%; vertical-align:top;">
    <p>
     <b>
      M4A
     </b>
 

In [6]:
table_contents=[]
table=data.find('table')
for row in table.findAll('td'):
    cell = {}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['Postal Code'] = row.p.text[:3]
        cell['Borough'] = (row.span.text).split('(')[0]
        cell['Neighborhood'] = (((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
        table_contents.append(cell)

# print(table_contents)
table_contents

[{'Postal Code': 'M3A', 'Borough': 'North York', 'Neighborhood': 'Parkwoods'},
 {'Postal Code': 'M4A',
  'Borough': 'North York',
  'Neighborhood': 'Victoria Village'},
 {'Postal Code': 'M5A',
  'Borough': 'Downtown Toronto',
  'Neighborhood': 'Regent Park, Harbourfront'},
 {'Postal Code': 'M6A',
  'Borough': 'North York',
  'Neighborhood': 'Lawrence Manor, Lawrence Heights'},
 {'Postal Code': 'M7A',
  'Borough': "Queen's Park",
  'Neighborhood': 'Ontario Provincial Government'},
 {'Postal Code': 'M9A',
  'Borough': 'Etobicoke',
  'Neighborhood': 'Islington Avenue'},
 {'Postal Code': 'M1B',
  'Borough': 'Scarborough',
  'Neighborhood': 'Malvern, Rouge'},
 {'Postal Code': 'M3B',
  'Borough': 'North York',
  'Neighborhood': 'Don Mills North'},
 {'Postal Code': 'M4B',
  'Borough': 'East York',
  'Neighborhood': 'Parkview Hill, Woodbine Gardens'},
 {'Postal Code': 'M5B',
  'Borough': 'Downtown Toronto',
  'Neighborhood': 'Garden District, Ryerson'},
 {'Postal Code': 'M6B', 'Borough': 'Nort

In [7]:
df=pd.DataFrame(table_contents)
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})

In [8]:
df.shape

(103, 3)

In [9]:
df

Postal Code                 Borough  \
0           M3A              North York   
1           M4A              North York   
2           M5A        Downtown Toronto   
3           M6A              North York   
4           M7A            Queen's Park   
5           M9A               Etobicoke   
6           M1B             Scarborough   
7           M3B              North York   
8           M4B               East York   
9           M5B        Downtown Toronto   
10          M6B              North York   
11          M9B               Etobicoke   
12          M1C             Scarborough   
13          M3C              North York   
14          M4C               East York   
15          M5C        Downtown Toronto   
16          M6C                    York   
17          M9C               Etobicoke   
18          M1E             Scarborough   
19          M4E            East Toronto   
20          M5E        Downtown Toronto   
21          M6E                    York   
22          M1G             Scarborough   
23          M4G               East York   
24          M5G        Downtown Toronto   
25          M6G        Downtown Toronto   
26          M1H             Scarborough   
27          M2H              North York   
28          M3H              North York   
29          M4H               East York   
30          M5H        Downtown Toronto   
31          M6H            West Toronto   
32          M1J             Scarborough   
33          M2J              North York   
34          M3J              North York   
35          M4J  East York/East Toronto   
36          M5J        Downtown Toronto   
37          M6J            West Toronto   
38          M1K             Scarborough   
39          M2K              North York   
40          M3K              North York   
41          M4K            East Toronto   
42          M5K        Downtown Toronto   
43          M6K            West Toronto   
44          M1L             Scarborough   
45          M2L              North York   
46          M3L              North York   
47          M4L            East Toronto   
48          M5L        Downtown Toronto   
49          M6L              North York   
50          M9L              North York   
51          M1M             Scarborough   
52          M2M              North York   
53          M3M              North York   
54          M4M            East Toronto   
55          M5M              North York   
56          M6M                    York   
57          M9M              North York   
58          M1N             Scarborough   
59          M2N              North York   
60          M3N              North York   
61          M4N         Central Toronto   
62          M5N         Central Toronto   
63          M6N                    York   
64          M9N                    York   
65          M1P             Scarborough   
66          M2P              North York   
67          M4P         Central Toronto   
68          M5P         Central Toronto   
69          M6P            West Toronto   
70          M9P               Etobicoke   
71          M1R             Scarborough   
72          M2R              North York   
73          M4R         Central Toronto   
74          M5R         Central Toronto   
75          M6R            West Toronto   
76          M7R             Mississauga   
77          M9R               Etobicoke   
78          M1S             Scarborough   
79          M4S         Central Toronto   
80          M5S        Downtown Toronto   
81          M6S            West Toronto   
82          M1T             Scarborough   
83          M4T         Central Toronto   
84          M5T        Downtown Toronto   
85          M1V             Scarborough   
86          M4V         Central Toronto   
87          M5V        Downtown Toronto   
88          M8V               Etobicoke   
89          M9V               Etobicoke   
90          M1W             Scarborough   
91          M4W        Downtown Toronto   
92   

# Second Part: Get the latitude and the longitude coordinates ofeach neighborhood.

In [10]:
url2 = 'https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs_v1/Geospatial_Coordinates.csv'
geotable = pd.read_csv(url2)
geotable.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [11]:
toronto = pd.merge(df, geotable, left_on='Postal Code', right_on='Postal Code', left_index=False, right_index=False)
toronto.head()

Postal Code           Borough                      Neighborhood   Latitude  \
0         M3A        North York                         Parkwoods  43.753259   
1         M4A        North York                  Victoria Village  43.725882   
2         M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3         M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4         M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

In [12]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(toronto['Borough'].unique()),
        toronto.shape[0]
))

The dataframe has 15 boroughs and 103 neighborhoods.


# Third part: Explore and cluster the neighborhoods in Toronto

In [13]:
address = 'Toronto'

geolocator = Nominatim(user_agent="Toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [14]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto['Latitude'], toronto['Longitude'], toronto['Borough'], toronto['Neighborhood']):
    label = '{}, {}'.format(toronto, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [15]:
CLIENT_ID = 'DE0OR0AXUKDZFS25UM4DALLMJ5PST4OBRRDRYYVP1TATKE3A' # your Foursquare ID
CLIENT_SECRET = 'SNC5NNSSP1LTTE23U4VH2ZIF3IV5GSWZJFBVIY4UYRRUNCHS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: DE0OR0AXUKDZFS25UM4DALLMJ5PST4OBRRDRYYVP1TATKE3A
CLIENT_SECRET:SNC5NNSSP1LTTE23U4VH2ZIF3IV5GSWZJFBVIY4UYRRUNCHS


In [16]:
toronto.loc[0, 'Neighborhood']

'Parkwoods'

In [17]:
neighborhood_latitude = toronto.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = toronto.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = toronto.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


In [18]:
LIMIT = 100
radius = 500 
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=DE0OR0AXUKDZFS25UM4DALLMJ5PST4OBRRDRYYVP1TATKE3A&client_secret=SNC5NNSSP1LTTE23U4VH2ZIF3IV5GSWZJFBVIY4UYRRUNCHS&v=20180605&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [19]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '608ec7b3a1b2400378e35482'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 43.757758604500005,
    'lng': -79.32343823984928},
   'sw': {'lat': 43.7487585955, 'lng': -79.33587476015072}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': 

In [20]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [21]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/srv/conda/envs/notebook/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114

In [22]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

2 venues were returned by Foursquare.


In [23]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [24]:
toronto_venues = getNearbyVenues(names=toronto['Neighborhood'],
                                   latitudes=toronto['Latitude'],
                                   longitudes=toronto['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Don Mills North
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
The Danforth  East
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmount Park
Bayview Village
Downsview East
The Danforth

In [25]:
print(toronto_venues.shape)
toronto_venues.head()

(2132, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3               Portugril       43.725819       -79.312785   
4             Tim Hortons       43.725517       -79.313103   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3  Portuguese Restaurant  
4            Coffee Shop

In [26]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                  6   
Bathurst Manor, Wilson Heights, Downsview North                        22   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      24   
Berczy Park                                                            58   
Birch Cliff, Cliffside West                                             5   
Brockton, Parkdale Village, Exhibition Place                           23   
CN Tower, King and Spadina, Railway Lands, Harb...                     15   
Caledonia-Fairbanks                                                     4   
Cedarbrae                                                               9   
Central Bay Street                                                     60   
Christie                                                               16   
Church and Wellesley                                                   76   
Clairville, Humberwood, Woodbine Downs, West Hu...                      4   
Clarks Corners, Tam O'Shanter, Sullivan                                14   
Cliffside, Cliffcrest, Scarborough Village West                         2   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             35   
Davisville North                                                        9   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        5   
Don Mills North                                                         7   
Don Mills South                                                        20   
Dorset Park, Wexford Heights, Scarborough Town ...                      6   
Downsview Central                                                       4   
Downsview East                                                          3   
Downsview Northwest                                                     5   
Downsview West                                                          5   
Dufferin, Dovercourt Village                                           16   
Enclave of L4W                                                         13   
Enclave of M4L                                                         16   
Enclave of M5E                                                        100   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      8   
Fairview, Henry Farm, Oriole                                           68   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                         8   
Guildwood, Morningside, West Hill                                       9   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          25   
Hillcrest Village                                                       5   
Humber Summit                                                           2   
Humberlea, Emery                                                        1   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         23   
Kennedy Park, Ionview, East Birchmount Park                             6   
Kensington Market, Chinatown, Grange Park                              65   
Kingsview Village, St. Phillips, Martin Grove G...                      3   
Lawrence Manor, Lawrence Heights                

In [27]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 271 uniques categories.


In [28]:
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Airport  \
0            0                  0               0        0   
1            0                  0               0        0   
2            0                  0               0        0   
3            0                  0               0        0   
4            0                  0               0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                    0             0         0            0           0   
1                    0             0         0            0           0   
2                    0             0         0            0           0   
3                    0             0         0            0           0   
4                    0             0         0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0          0       0           0              0          0         0   
1          0       0           0              0          0         0   
2          0       0           0              0          0         0   
3          0       0           0              0          0         0   
4          0       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Burger Joint  Burrito Place  Bus Line  Bus Station  \
0                0        

In [29]:
toronto_onehot.shape

(2132, 271)

In [30]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.000000   
8   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
9                                 Caledonia-Fairbanks     0.000000   
10                                          Cedarbrae     0.000000   
11                                 Central Bay Street     0.016667   
12                                           Christie     0.000000   
13                               Church and Wellesley     0.026316   
14  Clairville, Humberwood, Woodbine Downs, West H...     0.000000   
15            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
16    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
17                     Commerce Court, Victoria Hotel     0.000000   
18                                         Davisville     0.000000   
19                                   Davisville North     0.000000   
20   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
21                                    Don Mills North     0.000000   
22                                    Don Mills South     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                  Downsview Central     0.000000   
25                                     Downsview East     0.000000   
26                                Downsview Northwest     0.000000   
27                                     Downsview West     0.000000   
28                       Dufferin, Dovercourt Village     0.000000   
29                                     Enclave of L4W     0.000000   
30                                     Enclave of M4L     0.000000   
31                                     Enclave of M5E     0.010000   
32  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
33                       Fairview, Henry Farm, Oriole     0.000000   
34             First Canadian Place, Underground city     0.000000   
35                           Forest Hill North & West     0.000000   
36                           Garden District, Ryerson     0.000000   
37                                          Glencairn     0.000000   
38                    Golden Mile, Clairlea, Oakridge     0.000000   
39                  Guildwood, Morningside, West Hill     0.000000   
40  Harbourfront East, Union Station, Toronto Islands     0.000000   
41                      High Park, The Junction South     0.000000   
42                                  Hillcrest Village     0.000000   
43                                      Humber Summit     0.000000   
44                                   Humberlea, Emery     0.000000   
45                                 Humewood-Cedarvale     0.000000   
46                     India Bazaar, The Beaches West     0.000000   
47        Kennedy Park, Ionview, East Birchmount Park     0.000000   
48          Kensington Market, Chinatown, Grange Park     0.000000   
49  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
50                   Lawrence Manor, Lawrence Heights     0.000000   
51                                      Lawrence Park     0.000000   
52                                            Leaside     0.000000   
53                           Little Portugal, Trinity     0.023256   
54                                     Malvern, Rouge     0.000000   
55  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
56  Mimico NW, The Queensway West, South of Bloor,.

In [31]:
toronto_grouped.shape

(98, 271)

In [32]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                       venue  freq
0                     Lounge  0.25
1  Latin American Restaurant  0.25
2             Breakfast Spot  0.25
3             Clothing Store  0.25
4  Middle Eastern Restaurant  0.00


----Alderwood, Long Branch----
            venue  freq
0     Pizza Place  0.33
1             Pub  0.17
2  Sandwich Place  0.17
3             Gym  0.17
4     Coffee Shop  0.17


----Bathurst Manor, Wilson Heights, Downsview North----
                       venue  freq
0                Coffee Shop  0.09
1                       Bank  0.09
2                       Park  0.05
3              Shopping Mall  0.05
4  Middle Eastern Restaurant  0.05


----Bayview Village----
                 venue  freq
0                 Café  0.25
1  Japanese Restaurant  0.25
2                 Bank  0.25
3   Chinese Restaurant  0.25
4          Yoga Studio  0.00


----Bedford Park, Lawrence Manor East----
                venue  freq
0  Italian Restaurant  0.08
1      Sandwich Place  0.08

In [33]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [34]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood      1st Most Common Venue  \
0                                        Agincourt  Latin American Restaurant   
1                           Alderwood, Long Branch                Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                       Bank   
3                                  Bayview Village                       Café   
4                Bedford Park, Lawrence Manor East                Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                Lounge        Clothing Store        Breakfast Spot   
1                   Gym                   Pub        Sandwich Place   
2           Coffee Shop         Shopping Mall            Restaurant   
3                  Bank   Japanese Restaurant    Chinese Restaurant   
4            Restaurant    Italian Restaurant        Sandwich Place   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0         Women's Store             Drugstore        Discount Store   
1           Coffee Shop    Dim Sum Restaurant                 Diner   
2         Deli / Bodega      Sushi Restaurant        Ice Cream Shop   
3          Dessert Shop                 Diner        Discount Store   
4           Pizza Place      Sushi Restaurant               Butcher   

       8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0        Distribution Center               Dog Run       Doner Restaurant  
1             Discount Store   Distribution Center                Dog Run  
2  Middle Eastern Restaurant     Mobile Phone Shop     Chinese Restaurant  
3        Distribution Center               Dog Run       Doner Restaurant  
4                        Pub  Fast Food Restaurant        Thai Restaurant

In [35]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 3], dtype=int32)

In [36]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto

toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!


Postal Code           Borough                      Neighborhood   Latitude  \
0         M3A        North York                         Parkwoods  43.753259   
1         M4A        North York                  Victoria Village  43.725882   
2         M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3         M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4         M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -79.329656             3.0                  Park     Food & Drink Shop   
1 -79.315572             0.0          Intersection           Pizza Place   
2 -79.360636             0.0           Coffee Shop                   Pub   
3 -79.464763             0.0        Clothing Store          Carpet Store   
4 -79.389494             0.0           Coffee Shop      Sushi Restaurant   

  3rd Most Common Venue  4th Most Common Venue   5th Most Common Venue  \
0         Women's Store             Donut Shop                   Diner   
1           Coffee Shop  Portuguese Restaurant            Hockey Arena   
2                Bakery                   Park                    Café   
3           Coffee Shop     Miscellaneous Shop  Furniture / Home Store   
4           Yoga Studio                Theater                    Café   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Discount Store   Distribution Center               Dog Run   
1         Women's Store      Doner Restaurant    Dim Sum Restaurant   
2            Restaurant        Breakfast Spot               Theater   
3    Athletics & Sports   Arts & Crafts Store              Boutique   
4                   Bar                  Bank        Discount Store   

   9th Most Common Venue 10th Most Common Venue  
0       Doner Restaurant              Drugstore  
1                  Diner         Discount Store  
2   Gym / Fitness Center      Electronics Store  
3  Vietnamese Restaurant      Accessories Store  
4    Distribution Center     Mexican Restaurant

In [37]:
toronto_merged.dropna(inplace=True)
toronto_merged

Postal Code                 Borough  \
0           M3A              North York   
1           M4A              North York   
2           M5A        Downtown Toronto   
3           M6A              North York   
4           M7A            Queen's Park   
6           M1B             Scarborough   
7           M3B              North York   
8           M4B               East York   
9           M5B        Downtown Toronto   
10          M6B              North York   
12          M1C             Scarborough   
13          M3C              North York   
14          M4C               East York   
15          M5C        Downtown Toronto   
16          M6C                    York   
17          M9C               Etobicoke   
18          M1E             Scarborough   
19          M4E            East Toronto   
20          M5E        Downtown Toronto   
21          M6E                    York   
22          M1G             Scarborough   
23          M4G               East York   
24          M5G        Downtown Toronto   
25          M6G        Downtown Toronto   
26          M1H             Scarborough   
27          M2H              North York   
28          M3H              North York   
29          M4H               East York   
30          M5H        Downtown Toronto   
31          M6H            West Toronto   
32          M1J             Scarborough   
33          M2J              North York   
34          M3J              North York   
35          M4J  East York/East Toronto   
36          M5J        Downtown Toronto   
37          M6J            West Toronto   
38          M1K             Scarborough   
39          M2K              North York   
40          M3K              North York   
41          M4K            East Toronto   
42          M5K        Downtown Toronto   
43          M6K            West Toronto   
44          M1L             Scarborough   
46          M3L              North York   
47          M4L            East Toronto   
48          M5L        Downtown Toronto   
49          M6L              North York   
50          M9L              North York   
51          M1M             Scarborough   
53          M3M              North York   
54          M4M            East Toronto   
55          M5M              North York   
56          M6M                    York   
57          M9M              North York   
58          M1N             Scarborough   
59          M2N              North York   
60          M3N              North York   
61          M4N         Central Toronto   
62          M5N         Central Toronto   
63          M6N                    York   
64          M9N                    York   
65          M1P             Scarborough   
66          M2P              North York   
67          M4P         Central Toronto   
68          M5P         Central Toronto   
69          M6P            West Toronto   
70          M9P               Etobicoke   
71          M1R             Scarborough   
72          M2R              North York   
73          M4R         Central Toronto   
74          M5R         Central Toronto   
75          M6R            West Toronto   
76          M7R             Mississauga   
77          M9R               Etobicoke   
78          M1S             Scarborough   
79          M4S         Central Toronto   
80          M5S        Downtown Toronto   
81          M6S            West Toronto   
82          M1T             Scarborough   
83          M4T         Central Toronto   
84          M5T        Downtown Toronto   
85          M1V             Scarborough   
86          M4V         Central Toronto   
87          M5V        Downtown Toronto   
88          M8V               Etobicoke   
89          M9V               Etobicoke   
90          M1W             Scarborough   
91          M4W        Downtown Toronto   
92          M5W  Downtown Toronto Stn A   
93          M8W               Etobicoke   
94          M9W     Etobicoke Northwest   
96          M4X        Downtown Toronto   
97   

In [38]:
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype(int)

In [39]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map

markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + 'Cluster' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters